# **evaluation**

**Mean Average Precision(MAP)**

In [6]:
def calculate_map(sorted_documents, releation):
    total_precision = 0
    num_queries = 0

    for query_id, documents in sorted_documents.items():
        # Get the list of positive documents
        positive_list = releation.loc[releation['query_id'] == query_id, 'doc_id'].tolist()

        precision_sum = 0
        num_positives = len(positive_list)

        for i, doc_id in enumerate(documents):
            if doc_id in positive_list:
                precision_sum += precision_at_k(documents[:i+1], positive_list, i+1)

        if num_positives > 0:
            total_precision += precision_sum / num_positives
            num_queries += 1

    return total_precision / num_queries




**precision**

In [7]:
def precision_at_k(ranked_list, positive_list, k):

    if len(ranked_list) > k:
        ranked_list = ranked_list[:k]

    precision = 0
    correct = 0

    for i, p in enumerate(ranked_list):
        if p in positive_list and p not in ranked_list[:i]:
            correct += 1
            precision += correct / (i + 1)

    if not ranked_list:
        return 0

    return precision / len(ranked_list)

In [8]:
def calculate_precision_at_k(sorted_documents, releation, k):
    total_precision = 0
    num_queries = 0

    for query_id, documents in sorted_documents.items():
        # Get the list of positive documents
        positive_list = releation.loc[releation['query_id'] == query_id, 'doc_id'].tolist()

        precision = precision_at_k(documents, positive_list, k)

        total_precision += precision
        num_queries += 1

    return total_precision / num_queries



**mean reciprocal rank**

In [9]:
def calculate_mrr(sorted_documents, releation):
    total_reciprocal_rank = 0
    num_queries = 0

    for query_id, documents in sorted_documents.items():
        # Get the list of positive documents
        positive_list = releation.loc[releation['query_id'] == query_id, 'doc_id'].tolist()

        reciprocal_rank = 0

        for i, doc_id in enumerate(documents):
            if doc_id in positive_list:
                reciprocal_rank = 1 / (i + 1)
                break

        if reciprocal_rank > 0:
            total_reciprocal_rank += reciprocal_rank
            num_queries += 1

    return total_reciprocal_rank / num_queries

# **unigram and bigram model**

In [10]:
import pandas as pd


documents = pd.read_csv("hw1_docs.csv")

queries = pd.read_csv("hw1_queries.csv")

releation = pd.read_csv("hw1_qrels.csv")


display(documents)
display(queries)
display(releation)

doc_id                                           document
0    2p7qrgx0  Since 2007, many cases of fever, thrombocytope...
1    25dcnext  BACKGROUND: Respiratory viral (RV) outbreaks i...
2    2jq626ye  A novel coronavirus (2019-nCoV) originating in...
3    270msv5l  • Several studies suggested Baricitinib as a p...
4    14x4uqq7  Evidence from the 2003 SARS epidemic and 2009 ...
..        ...                                                ...
745  1ebkagvv  OBJECTIVE: To retrospectively analyze the ches...
746  80dfqjql  Summary The novel human coronavirus SARS-CoV-2...
747  0fzwwluc  Objectives: Patients with novel coronavirus di...
748  105q161g  A number of virological, epidemiological and e...
749  15rcq4sh  We evaluated a virus-infected cell-based indir...

[750 rows x 2 columns]

query_id                                              query
0          1                     what is the origin of COVID-19
1          2  how does the coronavirus respond to changes in...
2          3  will SARS-CoV2 infected people develop immunit...
3          4                   what causes death from Covid-19?
4          5  what drugs have been active against SARS-CoV o...
5          6  what types of rapid testing for Covid-19 have ...
6          7  are there serological tests that detect antibo...
7          8  how has lack of testing availability led to un...
8          9                   how has COVID-19 affected Canada
9         10  has social distancing had an impact on slowing...
10        11  what are the guidelines for triaging patients ...
11        12  what are best practices in hospitals and at ho...
12        13   what are the transmission routes of coronavirus?
13        14  what evidence is there related to COVID-19 sup...
14        15  how long can the coronavirus live outside the ...
15        16  how long does coronavirus remain stable  on su...
16        17  are there any clinical trials available for th...
17        18  what are the best masks for preventing infecti...
18        19  what type of hand sanitizer is needed to destr...
19        20  are patients taking Angiotensin-converting enz...
20        21  what are the mortality rates overall and in sp...
21        22  are cardiac complications likely in patients w...
22        23  what kinds of complications related to COVID-1...
23        24  what kinds of complications related to COVID-1...
24        25  which biomarkers predict the severe clinical c...
25        26         what are the initial symptoms of Covid-19?
26        27  what is known about those infected with Covid-...
27        28  what evidence is there for the value of hydrox...
28        29  which SARS-CoV-2 proteins-human proteins inter...
29        30  is remdesivir an effective treatment for COVID-19
30        31  How does the coronavirus differ from seasonal ...
31        32  Does SARS-CoV-2 have any subtypes, and if so w...
32        33  What vaccine candidates are being tested for C...
33        34  What are the longer-term complications of thos...
34        35  What new public datasets are available related...
35        36  What is the protein structure of the SARS-CoV-...
36        37  What is the result of phylogenetic analysis of...
37        38  What is the mechanism of inflammatory response...
38        39  What is the mechanism of cytokine storm syndro...
39        40  What are the observed mutations in the SARS-Co...
40        41  What are the impacts of COVID-19 among African...
41        42  Does Vitamin D impact COVID-19 prevention and ...
42        43  How has the COVID-19 pandemic impacted violenc...
43        44  How much impact do masks have on preventing th...
44        45  How has the COVID-19 pandemic impacted mental ...
45        46  what evidence is there for dexamethasone as a ...
46        47  what are the health outcomes for children who ...
47        48  what are the benefits and risks of re-opening ...
48        49  do individuals who recover from COVID-19 show ...
49        50  what is known about an mRNA vaccine for the SA...

query_id    doc_id
0           1  005b2j4b
1           1  0chuwvg6
2           1  0t2a5500
3           1  0y34yxlb
4           1  105q161g
..        ...       ...
745        50  xhm97wy2
746        50  xieqswct
747        50  y87tq9wu
748        50  ygwdldae
749        50  ykzsoafe

[750 rows x 2 columns]

In [11]:
import pandas as pd
import numpy as np
import re
from gensim.utils import simple_preprocess

from gensim.parsing.preprocessing import STOPWORDS

def preprocess(text):
   # Convert text to lowercase
   text = text.lower()
   # Remove special characters
   text = re.sub(r'\W', ' ', text)
   text = re.sub(r'\s+', ' ', text)
   # Tokenize the text
   words = simple_preprocess(text, deacc=True)

   # Remove stop words
   words = [word for word in words if word not in STOPWORDS]


   return words



In [12]:
queries['preprocessed_text'] = queries['query'].apply(preprocess)
documents['preprocessed_text'] = documents['document'].apply(preprocess)


In [13]:
display(documents)
display(queries)
display(releation)

doc_id                                           document  \
0    2p7qrgx0  Since 2007, many cases of fever, thrombocytope...   
1    25dcnext  BACKGROUND: Respiratory viral (RV) outbreaks i...   
2    2jq626ye  A novel coronavirus (2019-nCoV) originating in...   
3    270msv5l  • Several studies suggested Baricitinib as a p...   
4    14x4uqq7  Evidence from the 2003 SARS epidemic and 2009 ...   
..        ...                                                ...   
745  1ebkagvv  OBJECTIVE: To retrospectively analyze the ches...   
746  80dfqjql  Summary The novel human coronavirus SARS-CoV-2...   
747  0fzwwluc  Objectives: Patients with novel coronavirus di...   
748  105q161g  A number of virological, epidemiological and e...   
749  15rcq4sh  We evaluated a virus-infected cell-based indir...   

                                     preprocessed_text  
0    [cases, fever, leukopenia, syndrome, ftls, eme...  
1    [background, respiratory, viral, rv, outbreaks...  
2    [novel, coronavirus, ncov, originating, wuhan,...  
3    [studies, suggested, baricitinib, potential, d...  
4    [evidence, sars, epidemic, pandemic, shows, fa...  
..                                                 ...  
745  [objective, retrospectively, analyze, chest, c...  
746  [summary, novel, human, coronavirus, sars, cov...  
747  [objectives, patients, novel, coronavirus, dis...  
748  [number, virological, epidemiological, ethnogr...  
749  [evaluated, virus, infected, cell, based, indi...  

[750 rows x 3 columns]

query_id                                              query  \
0          1                     what is the origin of COVID-19   
1          2  how does the coronavirus respond to changes in...   
2          3  will SARS-CoV2 infected people develop immunit...   
3          4                   what causes death from Covid-19?   
4          5  what drugs have been active against SARS-CoV o...   
5          6  what types of rapid testing for Covid-19 have ...   
6          7  are there serological tests that detect antibo...   
7          8  how has lack of testing availability led to un...   
8          9                   how has COVID-19 affected Canada   
9         10  has social distancing had an impact on slowing...   
10        11  what are the guidelines for triaging patients ...   
11        12  what are best practices in hospitals and at ho...   
12        13   what are the transmission routes of coronavirus?   
13        14  what evidence is there related to COVID-19 sup...   
14        15  how long can the coronavirus live outside the ...   
15        16  how long does coronavirus remain stable  on su...   
16        17  are there any clinical trials available for th...   
17        18  what are the best masks for preventing infecti...   
18        19  what type of hand sanitizer is needed to destr...   
19        20  are patients taking Angiotensin-converting enz...   
20        21  what are the mortality rates overall and in sp...   
21        22  are cardiac complications likely in patients w...   
22        23  what kinds of complications related to COVID-1...   
23        24  what kinds of complications related to COVID-1...   
24        25  which biomarkers predict the severe clinical c...   
25        26         what are the initial symptoms of Covid-19?   
26        27  what is known about those infected with Covid-...   
27        28  what evidence is there for the value of hydrox...   
28        29  which SARS-CoV-2 proteins-human proteins inter...   
29        30  is remdesivir an effective treatment for COVID-19   
30        31  How does the coronavirus differ from seasonal ...   
31        32  Does SARS-CoV-2 have any subtypes, and if so w...   
32        33  What vaccine candidates are being tested for C...   
33        34  What are the longer-term complications of thos...   
34        35  What new public datasets are available related...   
35        36  What is the protein structure of the SARS-CoV-...   
36        37  What is the result of phylogenetic analysis of...   
37        38  What is the mechanism of inflammatory response...   
38        39  What is the mechanism of cytokine storm syndro...   
39        40  What are the observed mutations in the SARS-Co...   
40        41  What are the impacts of COVID-19 among African...   
41        42  Does Vitamin D impact COVID-19 prevention and ...   
42        43  How has the COVID-19 pandemic impacted violenc...   
43        44  How much impact do masks have on preventing th...   
44        45  How has the COVID-19 pandemic impacted mental ...   
45        46  what evidence is there for dexamethasone as a ...   
46        47  what are the health outcomes for children who ...   
47        48  what are the benefits and risks of re-opening ...   
48        49  do individuals who recover from COVID-19 show ...   
49        50  what is known about an mRNA vaccine for the SA...   

                                    preprocessed_text  
0                                     [origin, covid]  
1            [coronavirus, respond, changes, weather]  
2   [sars, cov, infected, people, develop, immunit...  
3                              [causes, death, covid]  
4   [drugs, active, sars, cov, sars, cov, animal, ...  
5           [types, rapid, testing, covid, developed]  
6   [serological, tests, detect, antibodies, coron...  
7   [lack, testing, availability, led, underreport...  
8                           [covid, affected, canada]  
9   [social, distancing, i

query_id    doc_id
0           1  005b2j4b
1           1  0chuwvg6
2           1  0t2a5500
3           1  0y34yxlb
4           1  105q161g
..        ...       ...
745        50  xhm97wy2
746        50  xieqswct
747        50  y87tq9wu
748        50  ygwdldae
749        50  ykzsoafe

[750 rows x 2 columns]

In [14]:
  # Flatten the preprocessed text data
flat_list = [item for sublist in documents['preprocessed_text'].tolist() for item in sublist]

# Generate unigrams
unigram = []
for word in flat_list:
    unigram.append(word)


In [15]:
print(flat_list)

['cases', 'fever', 'leukopenia', 'syndrome', 'ftls', 'emerged', 'henan', 'province', 'china', 'patient', 'reports', 'tick', 'bites', 'suggested', 'infection', 'contribute', 'ftls', 'tick', 'transmitted', 'microbial', 'pathogens', 'tested', 'pcr', 'rt', 'pcr', 'indirect', 'assay', 'ifa', 'samples', 'collected', 'tested', 'positive', 'human', 'granulocytic', 'anaplasmosis', 'hga', 'suggesting', 'pathogens', 'involved', 'unbiased', 'metagenomic', 'approach', 'screen', 'survey', 'microbes', 'possibly', 'associated', 'ftls', 'blastx', 'analysis', 'deduced', 'protein', 'sequences', 'revealed', 'novel', 'bunyavirus', 'identity', 'tehran', 'virus', 'accession', 'hq', 'present', 'sera', 'ftls', 'patients', 'phylogenetic', 'analysis', 'showed', 'closely', 'related', 'uukuniemi', 'virus', 'phlebovirus', 'genus', 'virus', 'distinct', 'candidate', 'virus', 'examined', 'association', 'ftls', 'samples', 'collected', 'henan', 'province', 'rt', 'pcr', 'viral', 'cultures', 'survey', 'undertaken', 'rt', 

In [16]:
print(unigram)

['cases', 'fever', 'leukopenia', 'syndrome', 'ftls', 'emerged', 'henan', 'province', 'china', 'patient', 'reports', 'tick', 'bites', 'suggested', 'infection', 'contribute', 'ftls', 'tick', 'transmitted', 'microbial', 'pathogens', 'tested', 'pcr', 'rt', 'pcr', 'indirect', 'assay', 'ifa', 'samples', 'collected', 'tested', 'positive', 'human', 'granulocytic', 'anaplasmosis', 'hga', 'suggesting', 'pathogens', 'involved', 'unbiased', 'metagenomic', 'approach', 'screen', 'survey', 'microbes', 'possibly', 'associated', 'ftls', 'blastx', 'analysis', 'deduced', 'protein', 'sequences', 'revealed', 'novel', 'bunyavirus', 'identity', 'tehran', 'virus', 'accession', 'hq', 'present', 'sera', 'ftls', 'patients', 'phylogenetic', 'analysis', 'showed', 'closely', 'related', 'uukuniemi', 'virus', 'phlebovirus', 'genus', 'virus', 'distinct', 'candidate', 'virus', 'examined', 'association', 'ftls', 'samples', 'collected', 'henan', 'province', 'rt', 'pcr', 'viral', 'cultures', 'survey', 'undertaken', 'rt', 

In [17]:
print(len(flat_list))

91122


In [18]:
freq_dist = pd.Series(unigram).value_counts()

In [19]:
print(freq_dist)
print(freq_dist.sum())

covid         1897
cov           1201
sars          1187
patients      1146
disease        683
              ... 
gaussian         1
parametric       1
wnv              1
htlv             1
fourfold         1
Length: 9489, dtype: int64
91122


## Calculate unigram Frequency

In [20]:
def calculate_unigram_frequncy(term, words):

    term_count = words.count(term)

    return term_count


In [21]:
import math

unigram_frequency = {}

# Iterate over the preprocessed documents
for i, row in documents.iterrows():
    # Get the preprocessed text for the current document
    preprocessed_words = row['preprocessed_text']
    # Calculate the term frequency for each word
    for word in preprocessed_words:
        if word not in unigram_frequency:
            unigram_frequency[word] = {}
        unigram_frequency[word][i] = calculate_unigram_frequncy(word, preprocessed_words)



In [22]:
print(unigram_frequency)
print(len(unigram_frequency))

{'cases': {0: 1, 14: 3, 26: 3, 30: 2, 35: 1, 37: 1, 41: 2, 49: 1, 51: 10, 54: 1, 58: 1, 62: 1, 63: 3, 67: 1, 69: 4, 72: 1, 77: 4, 78: 5, 82: 1, 87: 2, 93: 7, 98: 1, 99: 1, 100: 16, 105: 1, 111: 5, 112: 2, 114: 1, 115: 2, 117: 3, 118: 5, 119: 9, 123: 1, 126: 1, 128: 2, 129: 1, 133: 1, 134: 1, 137: 3, 138: 3, 144: 2, 147: 4, 148: 1, 150: 4, 153: 4, 154: 1, 159: 2, 160: 3, 162: 1, 169: 7, 186: 1, 191: 2, 192: 2, 194: 1, 200: 4, 205: 1, 206: 2, 207: 6, 208: 2, 209: 1, 210: 3, 215: 2, 216: 1, 217: 1, 218: 2, 219: 1, 220: 2, 221: 2, 238: 5, 239: 1, 240: 3, 241: 1, 249: 1, 250: 6, 252: 1, 253: 2, 255: 6, 258: 3, 261: 1, 264: 1, 265: 3, 268: 6, 275: 1, 281: 1, 283: 1, 287: 4, 289: 1, 290: 1, 297: 1, 299: 1, 303: 5, 308: 1, 309: 1, 312: 4, 317: 2, 318: 1, 321: 1, 325: 1, 329: 4, 332: 4, 336: 3, 345: 1, 348: 1, 352: 1, 356: 3, 371: 5, 377: 5, 378: 2, 379: 6, 384: 1, 387: 1, 390: 2, 401: 1, 402: 9, 404: 6, 406: 2, 407: 5, 412: 1, 415: 1, 420: 1, 422: 3, 426: 1, 428: 1, 430: 8, 431: 1, 437: 13, 44

## Calculate unigram Model

In [23]:
def calculate_unigram_model(_lambda, queries, documents, unigram_frequency, freq_dist):
   query_scores = {}
   sorted_documents_with_scores = {}
   for i, row in queries.iterrows():
        query_word = row['preprocessed_text']
        query_scores[row['query_id']] = {}
        for j, document in documents.iterrows():
            document_words = document['preprocessed_text']
            document_length = len(document_words)
            total_score = 1
            for word in query_word:
              if word in document_words:          # if word exists in words of document

                  score = _lambda * (unigram_frequency[word][j] / document_length) + (1 - _lambda) * (freq_dist[word] / freq_dist.sum()) # unigram formula

              elif word not in document_words:    # if word doesnt exist in words of document

                  if word in freq_dist:         # if word exists in words of document collection

                      score = (1 - _lambda) * (freq_dist[word] / freq_dist.sum())
                  else:
                      score = 0
              total_score *= score
            query_scores[row['query_id']][document['doc_id']] = total_score
    # Sort documents by scores

   for query_id, scores in query_scores.items():
        sorted_documents_with_scores [query_id] = sorted(scores, key=lambda x: scores[x], reverse=True)

   return sorted_documents_with_scores


In [24]:
def optimize_lambda_one(lambdas, queries, documents, unigram_frequency, freq_dist):

   best_lambda = None
   best_performance = 0

   for _lambda in lambdas:

      query_scores = calculate_unigram_model(_lambda, queries, documents, unigram_frequency, freq_dist)

       # Evaluate the performance

      performance_for_unigram = calculate_precision_at_k(query_scores, releation, 10)

      if performance_for_unigram > best_performance:
          best_lambda = _lambda
          best_performance = performance_for_unigram
   return best_lambda


In [25]:
lambdas = [0.01 , 0.05 , 0.1, 0.2, 0.3, 0.4, 0.5]



best_lambda = optimize_lambda_one(lambdas, queries, documents, unigram_frequency, freq_dist)

print(f"The best lambda value is {best_lambda}")


The best lambda value is 0.1


In [26]:
_lambda = 0.1  # best lambda from recent parts

query_docs_unigram = calculate_unigram_model(_lambda, queries, documents, unigram_frequency, freq_dist)



In [27]:
print(query_docs_unigram)

{1: ['lj8t52yl', '2y452utz', '0m5mc320', '0xkz36bj', '0cq5ee1i', '22fc1qly', '105q161g', '41378qru', '1vkz0b0o', '1mjaycee', '34ytd87a', '262bcl7h', '1sq2uvur', '1abp6oom', '4oa0gsos', '10ecm4wi', 'mgsaoz3j', '2nvk7glh', '5pv11lfo', '0gmtnkbh', '2zaxn6tq', '04zbbyii', '0uvzy48c', '1s0exznp', '0gikppdh', '427mkwsj', '0xqhm8a0', '42t0zriz', '5x30jj1s', '1nczw70h', '1xj2sg4y', '0kthumgi', '4r0t3q7j', '1cfwj5uq', '1hvihwkz', '2lxs9laj', '270msv5l', '6cm1vp7h', '0v1appqr', '2eterq28', '5kcl80sj', '178f21u7', '3cm44rbz', '27dmsmbu', '0pi8qur0', '1k3d3o2q', '0tsefy6p', '1y78dfsl', '0376d6vf', '09qp0sts', '0haf57l1', '45bwzuqn', '25v7qies', '9nbj3ckb', '1r8dhqi5', '0u00nhf2', '35izipky', '1i5arpf8', '1cpk2p9g', '7xqmuoye', '5bdoz5am', '401kxcmi', '3thnu3kk', 'kf7yz3oz', 'u35rryzi', '14ftgh6k', '2lebavgm', '0fkupng6', '0hgj2hcp', '0ec1cu8q', '4el6qq3n', '223v2obv', '1ge2dydz', '2boqg3tz', '0o92zije', '2pmpspuj', '0is1vyhy', '11es4w0u', '0vnewsci', '4pij0x9q', '1bhv9snq', '05zmldvj', '0nwmoua3',

## unigram evaluation

**print 10 best documents for a random query (unigram model)**

In [28]:
import random

# Select a random query
random_query_id = random.choice(list(query_docs_unigram.keys()))


original_query = queries.loc[queries['query_id'] == random_query_id, 'query'].values[0]

# Get the top 10 documents
top_10_documents = query_docs_unigram[random_query_id][:10]

print(f"For the query '{original_query}', the top 10 documents are: \n")
for doc_id in top_10_documents:
    document = documents.loc[documents['doc_id'] == doc_id]
    print(f"Document: {document['document'].values[0]}")


For the query 'will SARS-CoV2 infected people develop immunity? Is cross protection possible?', the top 10 documents are: 

Document: OBJECTIVE: The novel coronavirus pandemic is ravaging throughout the world. It has infected more than 1.2 million people and killed more than 64,000. Frantic research is underway to find prevention and cure. Of late, Bacillus Calmette–Guérin (BCG) has been speculated as a possible protection from COVID-19. We sought to investigate the evidence behind the claim. MATERIAL AND METHODS: Data were collected regarding the total number of COVID-19 cases per million and total number of COVID-19 deaths per million in various countries. The BCG vaccination policies of these countries were also obtained. RESULTS: It was seen that the countries with no universal BCG policy had a mean 1272.9 (median 795) cases per million and 80.7 deaths (median 18) per million population. On the contrary, the countries with a universal BCG vaccination policy had a mean 131.2 (median

In [29]:
p_at_5_unigram = calculate_precision_at_k(query_docs_unigram, releation, 5)

p_at_10_unigram  = calculate_precision_at_k(query_docs_unigram, releation, 10)

map_unigram = calculate_map(query_docs_unigram, releation)

mrr_unigram = calculate_mrr(query_docs_unigram, releation)


print(f"P@5 with unigram model: {p_at_5_unigram}")
print(f"P@10 with unigram model: {p_at_10_unigram}")
print(f"Mean Average Precision (MAP) with unigram model: {map_unigram}")
print(f"Mean Reciprocal Rank (MRR) with unigram model: {mrr_unigram}")


P@5 with unigram model: 0.43153333333333344
P@10 with unigram model: 0.3511293650793651
Mean Average Precision (MAP) with unigram model: 0.28998872851148344
Mean Reciprocal Rank (MRR) with unigram model: 0.69502958376333


## Calculate bigram Frequency

In [31]:
def calculate_bigram_frequency(bigram, bigrams):
 bigram_count = bigrams.count(bigram)
 return bigram_count

In [32]:

bigram_frequency = {}

for i, row in documents.iterrows():

 preprocessed_words = row['preprocessed_text']

 # Generate bigrams for the current document
 document_bigrams = [(preprocessed_words[i], preprocessed_words[i+1]) for i in range(len(preprocessed_words)-1)]

 # Calculate the bigram frequency for each bigram

 for bigram in document_bigrams:
     if bigram not in bigram_frequency:
         bigram_frequency[bigram] = {}
     bigram_frequency[bigram][i] = calculate_bigram_frequency(bigram, document_bigrams)


In [33]:
print(bigram_frequency)

{('cases', 'fever'): {0: 1}, ('fever', 'leukopenia'): {0: 1}, ('leukopenia', 'syndrome'): {0: 1}, ('syndrome', 'ftls'): {0: 1}, ('ftls', 'emerged'): {0: 1}, ('emerged', 'henan'): {0: 1}, ('henan', 'province'): {0: 2}, ('province', 'china'): {0: 1, 131: 1, 168: 1, 241: 1, 278: 1, 301: 1, 350: 2, 420: 1, 424: 1, 473: 1, 477: 1, 535: 1, 597: 1, 604: 1, 619: 2, 661: 1}, ('china', 'patient'): {0: 1}, ('patient', 'reports'): {0: 1}, ('reports', 'tick'): {0: 1}, ('tick', 'bites'): {0: 1}, ('bites', 'suggested'): {0: 1}, ('suggested', 'infection'): {0: 1}, ('infection', 'contribute'): {0: 1}, ('contribute', 'ftls'): {0: 1}, ('ftls', 'tick'): {0: 1}, ('tick', 'transmitted'): {0: 1}, ('transmitted', 'microbial'): {0: 1}, ('microbial', 'pathogens'): {0: 1}, ('pathogens', 'tested'): {0: 1}, ('tested', 'pcr'): {0: 1}, ('pcr', 'rt'): {0: 1, 343: 1}, ('rt', 'pcr'): {0: 3, 19: 1, 36: 1, 76: 2, 87: 2, 89: 1, 99: 2, 100: 1, 119: 1, 162: 4, 186: 2, 232: 5, 274: 1, 325: 1, 343: 1, 351: 1, 370: 3, 393: 1, 

## Calculate bigram Model

In [34]:
def calculate_score_for_first_query_word(first_query_word, document_words, document_length, unigram_frequency, freq_dist, _lambda , j ):

    # calculate 𝑃(𝑞1|𝐷)

   if first_query_word in document_words:

       score =( _lambda * (unigram_frequency[first_query_word][j] / document_length) +
               (1 - _lambda) * (freq_dist[first_query_word] / freq_dist.sum())
       )

   elif first_query_word not in document_words:

       if first_query_word in freq_dist:

           score = (1 - _lambda) * (freq_dist[first_query_word] / freq_dist.sum())

       else:

           score = 0

   return score

In [35]:
def calculate_score_for_second_to_end_of_query_words(bigram, document_bigrams, document_length, unigram_frequency, freq_dist, _lambda, _lambda_2 , j , bigram_frequency, document_words):

   if bigram in document_bigrams:

       score = (
           _lambda * (bigram_frequency[bigram][j] / unigram_frequency[bigram[0]][j]) +
           _lambda_2 * (unigram_frequency[bigram[1]][j] / document_length) +
           (1 - _lambda - _lambda_2) * (freq_dist[bigram[1]] / freq_dist.sum())
       )

   elif bigram[1] in document_words:  #second word of bigram exist in document

       score = (
           _lambda_2 * (unigram_frequency[bigram[1]][j] / document_length) +
           (1 - _lambda - _lambda_2) * (freq_dist[bigram[1]] / freq_dist.sum())
       )

   else:                              #second word of bigram doesnt exist in document


       if bigram[1] in freq_dist:          # if econd word of bigram exists in words of document collection

           score = (1 - _lambda - _lambda_2) * (freq_dist[bigram[1]] / freq_dist.sum())
       else:
           score = 0
   return score

In [36]:
def calculate_bigram_model(queries, documents, bigram_frequency, unigram_frequency, freq_dist, _lambda, _lambda_2 ):
   sorted_documents_with_scores = {}
   query_scores = {}

   for i, row in queries.iterrows():
       query_words = row['preprocessed_text']
       first_query_word = query_words[0]
       query_bigrams = [(query_words[i], query_words[i+1]) for i in range(len(query_words)-1)]

       query_scores[row['query_id']] = {}

       for j, document in documents.iterrows():
           document_words = document['preprocessed_text']
           document_bigrams = [(document_words[i], document_words[i+1]) for i in range(len(document_words)-1)]

           document_length = len( document_words )
           total_score = 1

           total_score *= calculate_score_for_first_query_word(first_query_word , document_words , document_length, unigram_frequency, freq_dist, _lambda , j)

           for bigram in query_bigrams :

               total_score *= calculate_score_for_second_to_end_of_query_words( bigram, document_bigrams, document_length, unigram_frequency, freq_dist, _lambda, _lambda_2 ,j ,bigram_frequency,document_words)

           query_scores[row['query_id']][document['doc_id']] = total_score


   for query_id, scores in query_scores.items():
        sorted_documents_with_scores [query_id] = sorted(scores, key=lambda x: scores[x], reverse=True)

   return sorted_documents_with_scores


In [37]:
def optimize_lambda_two(lambdas_two, queries, documents, unigram_frequency, freq_dist):

   best_lambda = None
   best_performance = 0

   _lambda =0.1

   for _lambda_2 in lambdas_two:

      query_scores = calculate_bigram_model(queries, documents, bigram_frequency, unigram_frequency, freq_dist, _lambda, _lambda_2 )

       # Evaluate the performance

      performance_for_bigram = calculate_precision_at_k(query_scores, releation, 10)

      if performance_for_bigram > best_performance:

          best_lambda = _lambda_2
          best_performance = performance_for_bigram

   return best_lambda


In [38]:
lambdas_two = [ 0.1, 0.2 , 0.4, 0.6 , 0.8]



best_lambda_2 = optimize_lambda_two(lambdas_two, queries, documents, unigram_frequency, freq_dist)

print(f"The best lambda two  value is {best_lambda_2}")


The best lambda two  value is 0.6


In [39]:
_lambda = 0.1
_lambda_2 = 0.6  # best lambda from recent parts

query_docs_bigram = calculate_bigram_model(queries, documents, bigram_frequency, unigram_frequency, freq_dist, _lambda, _lambda_2 )

print(query_docs_bigram)

{1: ['0m5mc320', 'lj8t52yl', '1mjaycee', '41378qru', '2y452utz', '34ytd87a', '0xkz36bj', '0cq5ee1i', '04zbbyii', '105q161g', '0uvzy48c', '1s0exznp', '0gikppdh', '427mkwsj', '0xqhm8a0', '42t0zriz', '5x30jj1s', '1nczw70h', '1xj2sg4y', '0kthumgi', '4r0t3q7j', '1cfwj5uq', '1hvihwkz', '2lxs9laj', '270msv5l', '6cm1vp7h', '0v1appqr', '2eterq28', '5kcl80sj', '178f21u7', '3cm44rbz', '27dmsmbu', '0pi8qur0', '1k3d3o2q', '0tsefy6p', '1y78dfsl', '0376d6vf', '09qp0sts', '0haf57l1', '22fc1qly', '45bwzuqn', '25v7qies', '9nbj3ckb', '1r8dhqi5', '0u00nhf2', '35izipky', '1i5arpf8', '1cpk2p9g', '7xqmuoye', '5bdoz5am', '401kxcmi', '3thnu3kk', 'kf7yz3oz', 'u35rryzi', '14ftgh6k', '2lebavgm', '0fkupng6', '0hgj2hcp', '0ec1cu8q', '4el6qq3n', '223v2obv', '1ge2dydz', '2boqg3tz', '0o92zije', '2pmpspuj', '0is1vyhy', '11es4w0u', '0vnewsci', '4pij0x9q', '1bhv9snq', '05zmldvj', '0nwmoua3', '1z6l12ks', '1n6d1gco', '12yk278d', '1mcl5yf1', '2071y2x8', '12ienbdx', '04esvfhp', '0l1jubg5', '1bxt21za', '1vkz0b0o', '04h53wjz',

## bigram evaluation

In [40]:
# Select a random query
random_query_id = random.choice(list(query_docs_bigram.keys()))


original_query = queries.loc[queries['query_id'] == random_query_id, 'query'].values[0]

# Get the top 10 documents
top_10_documents = query_docs_bigram[random_query_id][:10]

print(f"For the query '{original_query}', the top 10 documents are: \n")
for doc_id in top_10_documents:
    document = documents.loc[documents['doc_id'] == doc_id]
    print(f"Document: {document['document'].values[0]}")

For the query 'what are the health outcomes for children who contract COVID-19?', the top 10 documents are: 

Document: Abstract Background At present, coronavirus disease 2019 (COVID-19) has spread in many countries. We conducted this study to help paediatricians To help pediatricians understand the conditions of COVID-19 in children, we conducted this study. Methods We retrospectively summarized the characteristics, treatment and outcomes of pediatric cases in Wuhan children's hospital which was the only designated hospital for children with COVID-19 in Hubei Province. A Cox proportional hazards regression analysis was used to evaluate factors associated with clinical outcomes. Results As of February 29, 75 children had been discharged, of which only one was has severe pneumonia and one was critical cases. Children younger than 2 years were more susceptible to COVID-19. All patients have received interferon-α nebulization, and eight cases including the severe and critical cases were 

In [41]:
p_at_5_bigram = calculate_precision_at_k(query_docs_bigram, releation, 5)

p_at_10_bigram  = calculate_precision_at_k(query_docs_bigram, releation, 10)

map_bigram = calculate_map(query_docs_bigram, releation)

mrr_bigram = calculate_mrr(query_docs_bigram, releation)


print(f"P@5 with bigram model: {p_at_5_bigram}")
print(f"P@10 with bigram model: {p_at_10_bigram}")
print(f"Mean Average Precision (MAP) with bigram model: {map_bigram}")
print(f"Mean Reciprocal Rank (MRR) with bigram model: {mrr_bigram}")

P@5 with bigram model: 0.40053333333333335
P@10 with bigram model: 0.30060714285714285
Mean Average Precision (MAP) with bigram model: 0.2485198278575091
Mean Reciprocal Rank (MRR) with bigram model: 0.7330032679738561
